In [1]:
from IPython.display import display, SVG
from typing import Optional, Sequence
import dataclasses
import math
import enum

from typesetting import ParagraphItem, ParagraphItemType, Font, Glyph, hyphenate, text_to_paragraph_items, MAX_PENALTY, greedy_line_breaks, optimal_line_breaks
from typesetting.cairo import fill_glyphs_at

Source:

http://www.eprg.org/G53DOC/pdfs/knuth-plass-breaking.pdf

In [2]:
from faker import Faker
import textwrap

Faker.seed(0x01234567)
lorem = hyphenate("".join([
    "Difficult Quick Foxes with 1034 boxes. ",
    Faker(["en"]).paragraph(30)
]))
print(f"Generated lorem ipsum:\n\n{textwrap.fill(textwrap.shorten(lorem, 200), 72)}")
print(f"\nRepr of first part:\n{textwrap.shorten(lorem, 72)!r}")

Generated lorem ipsum:

Dif­fi­cult Quick Foxes with 1034 boxes. Ques­tion drug can­di­date.
Edge I mes­sage here. Ex­pert cold sci­en­tist can­di­date black brother
him. Worry per­haps talk pull blue let­ter. Gun [...]

Repr of first part:
'Dif\xadfi\xadcult Quick Foxes with 1034 boxes. Ques\xadtion drug [...]'


In [3]:
rm_face_path = "EBGaramond-VariableFont_wght.ttf"
#rm_face_path = "Raleway-VariableFont_wght.ttf"
#rm_face_path = "LibreBaskerville-Regular.ttf"
rm_size = 12
rm_font = Font(path=rm_face_path, em_size=[rm_size, rm_size], features=["onum"])

sm_rm_size = rm_size * 0.8
sm_rm_font = Font(path=rm_face_path, em_size=[sm_rm_size, sm_rm_size], features=["onum"])

In [4]:
import uniseg.linebreak
print(textwrap.fill("|".join(uniseg.linebreak.line_break_units(lorem)), 80))

Dif­|fi­|cult |Quick |Foxes |with |1034 |boxes. |Ques­|tion |drug
|can­|di­|date. |Edge |I |mes­|sage |here. |Ex­|pert |cold |sci­|en­|tist
|can­|di­|date |black |brother |him. |Worry |per­|haps |talk |pull |blue
|let­|ter. |Gun |choose |abil­|ity |fin­|ish. |Cut |decade |hun­|dred |whom
|short |past. |I |win |num­|ber |ta­|ble |party. |In­|di­|vid­|ual |laugh |end
|af­|fect |present |imag­|ine |body. |Hear |es­|tab­|lish |pay |go
|pol­|i­|tics. |Cell |re­|veal |sit |try |mem­|ory |own |op­|er­|a­|tion
|ma­|jor­|ity. |Player |old |ap­|ply |lan­|guage |hus­|band |ei­|ther. |Lawyer
|com­|mon |artist |space. |Through |tax |ac­|tion |ben­|e­|fit |pur­|pose |our
|you. |Change |they |trip |it­|self |grow |pol­|i­|tics |end |ar­|ti­|cle. |No
|an­|swer |in­|ter­|view |mil­|lion |oc­|cur. |Laugh |trade |your­|self |child
|reach |last. |Pic­|ture |push |owner |open |com­|mer­|cial |woman |space.
|Agree­|ment |re­|port |wrong |im­|por­|tant |source |tonight. |War
|op­|por­|tu­|nity |film |course 

In [5]:
para_items = list(text_to_paragraph_items(lorem, rm_font))

if False:
    print("First few items:")
    print("\n".join(textwrap.indent(f"{item!r}", "  ") for item in para_items[:10]))
    print("Final few items:")
    print("\n".join(textwrap.indent(f"{item!r}", "  ") for item in para_items[-10:]))

In [6]:
import io
from IPython.display import display, SVG
import cairo
from typing import Iterable

def render_lines(ctx: cairo.Context, line_break_idxs: Iterable[int], x0: float, y0: float, line_width: float):
    line_start_idx = 0
    for line_idx, line_end_idx in enumerate(line_break_idxs):
        x = x0
        y = line_height*line_idx + y0
        running_text, running_width = [], 0.0
    
        # What delta needs to be taken up by glue
        natural_width, total_stretch, total_shrink = 0.0, 0.0, 0.0
        for item in para_items[line_start_idx:line_end_idx]:
            if item.item_type == ParagraphItemType.PENALTY:
                continue
            natural_width += item.width
            if item.item_type == ParagraphItemType.GLUE:
                total_stretch += item.stretchability
                total_shrink += item.shrinkability
        if para_items[line_end_idx].item_type == ParagraphItemType.PENALTY:
            natural_width += para_items[line_end_idx].width
        delta = line_width - natural_width
    
        # Total slack for delta
        if delta > 0.0:
            adjustment_ratio = delta / total_stretch if total_stretch > 0 else math.inf
        elif delta < 0.0:
            adjustment_ratio = delta / total_shrink if total_shrink > 0 else math.inf
        else:
            adjustment_ratio = 0.0

        fill_glyphs_at(ctx, x + line_width + rm_font.em_size[0], y, sm_rm_font.shape(f"{adjustment_ratio:.2f}"), sm_rm_font)

        adjustment_ratio = max(-1.0, adjustment_ratio)
        for item_idx in range(line_start_idx, line_end_idx+1):
            item = para_items[item_idx]
            if item_idx != line_end_idx and item.item_type == ParagraphItemType.PENALTY:
                continue
            if item_idx == line_end_idx and item.item_type == ParagraphItemType.GLUE:
                continue
            running_width += item.width
            if item.item_type == ParagraphItemType.GLUE:
                text = "".join(running_text)
                fill_glyphs_at(ctx, x, y, rm_font.shape(text), rm_font)
                x += running_width
                if adjustment_ratio > 0:
                    x += item.stretchability * adjustment_ratio
                else:
                    x += item.shrinkability * adjustment_ratio
    
                running_text, running_width = [], 0.0
            else:
                running_text.append(item.text)
        text = "".join(running_text)
        if text != "":
            fill_glyphs_at(ctx, x, y, rm_font.shape(text), rm_font)
        line_start_idx = line_end_idx+1

In [7]:
line_width = 5 * 72

In [8]:
if True:
    %timeit list(greedy_line_breaks(para_items, line_width))
    %timeit list(optimal_line_breaks(para_items, line_width))
    %prun -s cumulative -q -D prun.stats [list(optimal_line_breaks(para_items, line_width)) for _ in range(10)]
    !gprof2dot -f pstats prun.stats >profile.dot

552 µs ± 56.6 µs per loop (mean ± std. dev. of 7 runs, 1,000 loops each)
6.15 ms ± 455 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)
 
*** Profile stats marshalled to file 'prun.stats'.


In [9]:
optimal_line_break_idxs = list(optimal_line_breaks(para_items, line_width))
greedy_line_break_idxs = list(greedy_line_breaks(para_items, line_width))
line_height = rm_size * 1.1
paper_size = (2 * (line_width + rm_font.em_size[0] * 5), line_height * (max(len(greedy_line_break_idxs), len(optimal_line_break_idxs)) + 2))

In [10]:
def draw_page(ctx: cairo.Context, line_break_idxs: Sequence[int], line_width: float, line_height: float):
    ctx.set_source_rgba(1, 0, 0, 0.5)
    ctx.set_line_width(1.0)

    ctx.move_to(rm_size, 0)
    ctx.rel_line_to(0, paper_size[1])
    ctx.move_to(rm_size + line_width, 0)
    ctx.rel_line_to(0, paper_size[1])
    ctx.close_path()
    ctx.stroke()
    
    ctx.set_source_rgb(0, 0, 0)
    render_lines(ctx, line_break_idxs, rm_size, 2*line_height, line_width)

svg_file = io.BytesIO()
with cairo.SVGSurface(svg_file, paper_size[0], paper_size[1]) as surface:
    ctx = cairo.Context(surface)
    ctx.set_source_rgb(1, 1, 1)
    ctx.rectangle(0, 0, paper_size[0], paper_size[1])
    ctx.fill()

    draw_page(ctx, greedy_line_break_idxs, line_width, line_height)
    ctx.translate(line_width + rm_font.em_size[0] * 5, 0)
    draw_page(ctx, optimal_line_break_idxs, line_width, line_height)
display(SVG(svg_file.getvalue()))

with cairo.PDFSurface("example.pdf", paper_size[0], paper_size[1]) as surface:
    ctx = cairo.Context(surface)
    ctx.set_source_rgb(1, 1, 1)
    ctx.rectangle(0, 0, paper_size[0], paper_size[1])
    ctx.fill()

    draw_page(ctx, greedy_line_break_idxs, line_width, line_height)
    ctx.translate(line_width + rm_font.em_size[0] * 5, 0)
    draw_page(ctx, optimal_line_break_idxs, line_width, line_height)